<h1><center>Laboratorio 9:  ¿Superhéroe o Villano?  🦴</center></h1>

<center><strong>MDS7202: Laboratorio de Programación Científica para Ciencia de Datos</strong></center>

### Cuerpo Docente:

- Profesor: Pablo Badilla y Ignacio Meza
- Auxiliar: Sebastián Tinoco
- Ayudante: Felipe Arias y Diego Cortez

### Equipo: SUPER IMPORTANTE - notebooks sin nombre no serán revisados

- Nombre de alumno 1: Diego Dominguez
- Nombre de alumno 2: Arturo Lazcano


\### **Link de repositorio de GitHub:** `https://github.com/DDominguezD/MDS7202`

## Temas a tratar

- Codificación de texto usando Bag of Words.
- Búsqueda del modelo óptimo de clasificación usando `GridSearch`
- Uso de pipelines.

## Reglas:

- **Grupos de 2 personas**
- Asistencia **obligatoria** a instrucciones del lab (viernes 16.15). Luego, pueden quedarse trabajando en las salas o irse.
- **No se revisarán entregas de personas ausentes**.
- Cualquier duda fuera del horario de clases al foro. Mensajes al equipo docente serán respondidos por este medio.
- Prohibidas las copias.
- Pueden usar cualquer material del curso que estimen conveniente.

### Objetivos principales del laboratorio

- Obtener caracteristicas a partir de texto usando `CountVectorizer`.
- Fijar un pipeline con un modelo base que luego se irá optimizando.
- Comprender como realizar una búsqueda de grilla sobre un conjunto de clasificadores e hiperparámetros usando `GridSearch`.

El laboratorio deberá ser desarrollado sin el uso indiscriminado de iteradores nativos de python (aka "for", "while"). La idea es que aprendan a exprimir al máximo las funciones optimizadas que nos entrega `pandas`, las cuales vale mencionar, son bastante más eficientes que los iteradores nativos sobre DataFrames.

#Importamos librerias utiles 😸

In [1]:
# Librería Core del lab.
import numpy as np
import pandas as pd
from sklearn.pipeline import Pipeline

from sklearn.model_selection import train_test_split

# Pre-procesamiento
from sklearn.feature_selection import SelectPercentile, f_classif
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import MinMaxScaler
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.preprocessing import FunctionTransformer

# Clasifación
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.dummy import DummyClassifier

# Metricas de evaluación
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import cohen_kappa_score

from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingGridSearchCV

# Librería para plotear
!pip install --upgrade plotly
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Librería para NLP
!pip install nltk
import nltk
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk import word_tokenize
from nltk.stem import PorterStemmer
nltk.download('stopwords')

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

# 1. ¿Quien es Bat Cow?

<p align="center">
  <img src="https://i.imgur.com/D9f1RHy.jpg" width="350">
</p>

En vez de estar desarrollando las evaluaciones correspondientes a su curso, su profesor de catedra y su auxiliar discuten acerca la alineación (héroe o villano) del personaje de ficción Bat-Cow.

El cuerpo docente, no logra ponerse de acuerdo si el personaje es bueno, neutral o malo: el auxiliar plantea que Bat-cow posee una siniestra mirada, intrigante pero común característica de los personajes malvados.
Por otra parte, extendiendo las ideas de Rousseau, el profesor plantea que tal como los humanos no nacen malos, no existe motivo por el cual una vaca con superpoderes deba serlo.

Sin embargo, ambos concuerdan que es difícil estimar la alineación solo usando los atributos físicos, por lo que creen el análisis debe ser complementado aún más antes de comunicarle los resultados a su estudiantado. Buscando más información, ambos sujetos se percatan de la existencia de un excelente antecedente para estimar la alineación: la historia personal de cada superhéroe o villano.

Es por esto le solicitan que construya y optimice un clasificador basado en texto el cual analice la alineación de cada personaje basado en su historia personal.

Para este laboratorio deben trabajar con los datos `df_comics.csv` y `comics_no_label.csv` subidos a u-cursos. El primero es un conjunto de datos que les servirá para entrenar un modelo de clasificación, mientras que el segundo es un dataset con personajes de ficción no etiquetados a predecir (sí, aquí está la misteriosa Batcow).

Para comenzar cargue los dataset señalados y visualice a través de un head los atributos que poseen cada uno de los dataset.


In [2]:
# Si usted está utilizando Colaboratory le puede ser útil este código para cargar los archivos.
#try:
#    from google.colab import drive
#    drive.mount("/content/drive")
#    path = 'Dirección donde tiene los archivos en el Drive'
#except:
#    print('Ignorando conexión drive-colab')

In [2]:
# --- [Se suben los archivos a google colab de forma local] ---

df_comics = pd.read_csv('df_comics.csv')
df_comics_no_label = pd.read_csv('comics_no_label.csv')
df_comics = df_comics.dropna(subset=['history_text']).reset_index(drop=True) # eliminar ejemplos sin historia

In [4]:
# queda a labor de su equipo hacer el análisis exploratorio
df_comics.head()

Unnamed: 0          name               real_name               full_name  \
0           0       3-D Man     Delroy Garrett, Jr.     Delroy Garrett, Jr.   
1           2        A-Bomb  Richard Milhouse Jones  Richard Milhouse Jones   
2           3            Aa                      Aa                     NaN   
3           4    Aaron Cash              Aaron Cash              Aaron Cash   
4           5  Aayla Secura            Aayla Secura                     NaN   

  overall_score                                       history_text  \
0             6  Delroy Garrett, Jr. grew up to become a track ...   
1            20   Richard "Rick" Jones was orphaned at a young ...   
2            12  Aa is one of the more passive members of the P...   
3             5  Aaron Cash is the head of security at Arkham A...   
4             8  ayla Secura was a Rutian Twi'lek Jedi Knight (...   

                                         powers_text  intelligence_score  \
0                                                NaN                  85   
1    On rare occasions, and through unusual circu...                  80   
2                                                NaN                  80   
3                                                NaN                  80   
4                                                NaN                  90   

   strength_score  speed_score  ...  has_flight  has_accelerated_healing  \
0              30           60  ...         0.0                      0.0   
1             100           80  ...         0.0                      1.0   
2              50           55  ...         0.0                      0.0   
3              10           25  ...         0.0                      0.0   
4              40           45  ...         0.0                      1.0   

   has_weapons_master has_intelligence has_reflexes has_super_speed  \
0                 0.0              0.0          0.0             1.0   
1                 0.0              0.0          1.0             1.0   
2                 0.0              0.0          0.0             0.0   
3                 1.0              0.0          0.0             0.0   
4                 0.0              0.0          0.0             0.0   

  has_durability has_stamina has_agility has_super_strength  
0            0.0         0.0         0.0                1.0  
1            1.0         1.0         1.0                1.0  
2            0.0         0.0         0.0                0.0  
3            0.0         0.0         0.0                0.0  
4            0.0         0.0         1.0                0.0  

[5 rows x 82 columns]

## EDA

In [3]:
# Eliminiar columna sin información (unnamed)
df_comics.drop('Unnamed: 0', axis=1, inplace=True)

In [4]:
# Dimensiones del dataframe
print('El dataframe tiene dimensiones (fil, col):', df_comics.shape)

El dataframe tiene dimensiones (fil, col): (1285, 81)


In [5]:
# Información del dataframe
df_comics.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1285 entries, 0 to 1284
Data columns (total 81 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   name                              1285 non-null   object 
 1   real_name                         1164 non-null   object 
 2   full_name                         895 non-null    object 
 3   overall_score                     1285 non-null   object 
 4   history_text                      1285 non-null   object 
 5   powers_text                       961 non-null    object 
 6   intelligence_score                1285 non-null   int64  
 7   strength_score                    1285 non-null   int64  
 8   speed_score                       1285 non-null   int64  
 9   durability_score                  1285 non-null   int64  
 10  power_score                       1285 non-null   int64  
 11  combat_score                      1285 non-null   int64  
 12  superp

In [6]:
# Descripción columnas numéricas del dataframe
df_comics.describe()

intelligence_score  strength_score  speed_score  durability_score  \
count         1285.000000     1285.000000  1285.000000       1285.000000   
mean            78.665370       38.832685    45.898833         55.610895   
std             25.074439       34.220845    29.176614         31.683003   
min              0.000000        0.000000     0.000000          0.000000   
25%             75.000000       10.000000    25.000000         30.000000   
50%             85.000000       30.000000    40.000000         55.000000   
75%             95.000000       65.000000    65.000000         85.000000   
max            100.000000      100.000000   100.000000        100.000000   

       power_score  combat_score  has_electrokinesis  has_energy_constructs  \
count  1285.000000   1285.000000         1228.000000            1228.000000   
mean     66.556420     67.805447            0.089577               0.074919   
std      33.329484     29.598315            0.285690               0.263367   
min       0.000000      0.000000            0.000000               0.000000   
25%      40.000000     55.000000            0.000000               0.000000   
50%      70.000000     75.000000            0.000000               0.000000   
75%     100.000000     90.000000            0.000000               0.000000   
max     100.000000    100.000000            1.000000               1.000000   

       has_mind_control_resistance  has_matter_manipulation  ...   has_flight  \
count                  1228.000000              1228.000000  ...  1228.000000   
mean                      0.074104                 0.046417  ...     0.265472   
std                       0.262047                 0.210472  ...     0.441764   
min                       0.000000                 0.000000  ...     0.000000   
25%                       0.000000                 0.000000  ...     0.000000   
50%                       0.000000                 0.000000  ...     0.000000   
75%                       0.000000                 0.000000  ...     1.000000   
max                       1.000000                 1.000000  ...     1.000000   

       has_accelerated_healing  has_weapons_master  has_intelligence  \
count              1228.000000         1228.000000       1228.000000   
mean                  0.307003            0.403909          0.429153   
std                   0.461439            0.490880          0.495157   
min                   0.000000            0.000000          0.000000   
25%                   0.000000            0.000000          0.000000   
50%                   0.000000            0.000000          0.000000   
75%                   1.000000            1.000000          1.000000   
max                   1.000000            1.000000          1.000000   

       has_reflexes  has_super_speed  has_durability  has_stamina  \
count   1228.000000      1228.000000     1228.000000  1228.000000   
mean       0.437296         0.387622        0.504886     0.540717   
std        0.496255         0.487406        0.500180     0.498542   
min        0.000000         0.000000        0.000000     0.000000   
25%        0.000000         0.000000        0.000000     0.000000   
50%        0.000000         0.000000        1.000000     1.000000   
75%        1.000000         1.000000        1.000000     1.000000   
max        1.000000         1.000000        1.000000     1.000000   

       has_agility  has_super_strength  
count  1228.000000         1228.000000  
mean      0.566775            0.522801  
std       0.495723            0.499683  
min       0.000000            0.000000  
25%       0.000000            0.000000  
50%       1.000000            1.000000  
75%       1.000000            1.000000  
max       1.000000            1.000000  

[8 rows x 56 columns]

In [7]:
# Ver nulos por columna
print('Cantidad de nulos por columnas:\n')
print(df_comics.isna().sum().to_string())

Cantidad de nulos por columnas:

name                                   0
real_name                            121
full_name                            390
overall_score                          0
history_text                           0
powers_text                          324
intelligence_score                     0
strength_score                         0
speed_score                            0
durability_score                       0
power_score                            0
combat_score                           0
superpowers                            0
alter_egos                             0
aliases                                0
place_of_birth                       551
first_appearance                     143
creator                              119
alignment                              0
occupation                           347
base                                 472
teams                                  0
relatives                            456
gender                  

In [8]:
# Ejemplos aleatorios
df_comics.sample(5)

name         real_name            full_name  \
541                  Hulk      Bruce Banner  Robert Bruce Banner   
375             Ego (MCU)               Ego                  NaN   
293               Cyclops     Scott Summers        Scott Summers   
170                 Blink  Clarice Ferguson     Clarice Ferguson   
981  Rocket Raccoon (MCU)    Rocket Raccoon                  NaN   

    overall_score                                       history_text  \
541            34    Robert Bruce Banner was the son of an alcoho...   
375            22  Ego was a Celestial, a primordial and an extre...   
293             8    Scott Summers was the first of two sons born...   
170             5    Blink was one of the many young mutants capt...   
981             9  Subject: 89P13 was recovered by alien scientis...   

                                           powers_text  intelligence_score  \
541  The Hulk is one of the most powerful beings in...                  60   
375  Ego is a Celestial, a primordial race of brain...                  90   
293    Cyclops possesses the mutant ability to proj...                  90   
170    Blink possesses the ability to generate tele...                  75   
981  Rocket's cerebral cortex was genetically enhan...                  95   

     strength_score  speed_score  durability_score  ...  has_flight  \
541             100           85               100  ...         0.0   
375              95           85                95  ...         1.0   
293              10           25                40  ...         0.0   
170              10           20                30  ...         0.0   
981              15           60                45  ...         0.0   

     has_accelerated_healing has_weapons_master has_intelligence has_reflexes  \
541                      1.0                0.0              0.0          1.0   
375                      0.0                0.0              1.0          0.0   
293                      0.0                0.0              1.0          0.0   
170                      0.0                0.0              0.0          0.0   
981                      0.0                1.0              1.0          0.0   

    has_super_speed has_durability has_stamina has_agility has_super_strength  
541             1.0            1.0         1.0         1.0                1.0  
375             0.0            1.0         0.0         0.0                1.0  
293             0.0            0.0         0.0         1.0                0.0  
170             0.0            0.0         0.0         0.0                0.0  
981             0.0            0.0         0.0         1.0                0.0  

[5 rows x 81 columns]

In [9]:
# Cantidad de valores únicos por columna
print(df_comics.nunique().to_string())

name                                1285
real_name                            971
full_name                            794
overall_score                         87
history_text                        1274
powers_text                          939
intelligence_score                    16
strength_score                        21
speed_score                           21
durability_score                      21
power_score                           21
combat_score                          21
superpowers                         1166
alter_egos                           463
aliases                              860
place_of_birth                       422
first_appearance                    1003
creator                               39
alignment                              3
occupation                           753
base                                 519
teams                                390
relatives                            775
gender                                 2
type_race       

## 1.1 Obtención de Features y Bag of Words

<p align="center">
  <img src="https://media0.giphy.com/media/eIUpSyzwGp0YhAMTKr/200.gif" width="300">
</p>

Primero que todo, deben obtener un vector de características del atributo `history_text`, utilizando `Bag of Words`. En este atributo se presenta una breve descripción de la historia de cada uno de los personajes de ficción presentes en el dataset.

Pero... antes de empezar, ¿Que es `Bag of Words`?...

`Bag of Words` es un modelo de conteo utilizado en Procesamiento de Lenguaje Natural (NLP) que tiene como objetivo generar una representación vectorial (vector de características en nuestro cas) para cada documento a través del conteo de las palabras que contienen.

La siguiente figura muestra un ejemplo de `Bag of Words` en acción:

<p align="center">
  <img src="https://user.oc-static.com/upload/2020/10/23/16034397439042_surfin%20bird%20bow.png" width="500">
</p>

Como pueden ver, el modelo de `Bag of Words` no resulta tan complicado, ¿pero cómo lo aplicamos en python?.

Como podrán darse cuenta del ejemplo anterior, para facilitar el conteo será necesario transformar cada uno de los documentos en vectores, donde cada una de las posiciones posee un carácter. Este proceso es conocido como **tokenización** y lo podemos realizar de la siguiente forma:

In [10]:
docs = ['The teacher rocks like a good rock & roll',
             'the rock is the best actor in the world']


docs_tokenizados = [word_tokenize(doc)  for doc in docs]
docs_tokenizados

[['The', 'teacher', 'rocks', 'like', 'a', 'good', 'rock', '&', 'roll'],
 ['the', 'rock', 'is', 'the', 'best', 'actor', 'in', 'the', 'world']]

Podemos mejorar un poco más el proceso de tokenización agregando

- Stemming:  Definimos Stemming como un algoritmo basado en reglas que transforma las palabras a una forma general. Un ejemplo de stemming, es el siguiente:
- Eliminación de Stopwords: Eliminación de palabras muy frecuentes que entorpecen la clasificación (por ejemplo, el, la los, la, etc...)

<p align="center">
  <img src="https://devopedia.org/images/article/218/8583.1569386710.png" width="300">
</p>


In [11]:

# Definimos algunas stopword que queremos que sean eliminadas
import nltk
nltk.download('stopwords')

from nltk.corpus import stopwords

#stop_words = stopwords.words('spanish')
stop_words = stopwords.words('english')

# Definimos un tokenizador con Stemming
class StemmerTokenizer:
    def __init__(self):
        self.ps = PorterStemmer()
    def __call__(self, doc):
        doc_tok = word_tokenize(doc)
        doc_tok = [t for t in doc_tok if t not in stop_words]
        return [self.ps.stem(t) for t in doc_tok]

# Inicializamos tokenizador
tokenizador = StemmerTokenizer()

# Creamos algunos documentos
docs = ['The teacher rocks like a good rock & roll',
        'the rock is the best actor in the world',
        'New York is a beautiful city']

# Obtenemos el token del primer documento
[tokenizador(doc) for doc in docs]

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[['the', 'teacher', 'rock', 'like', 'good', 'rock', '&', 'roll'],
 ['rock', 'best', 'actor', 'world'],
 ['new', 'york', 'beauti', 'citi']]

In [12]:
# Comparación con el caso anterior
docs_tokenizados = [word_tokenize(doc) for doc in docs]
docs_tokenizados

[['The', 'teacher', 'rocks', 'like', 'a', 'good', 'rock', '&', 'roll'],
 ['the', 'rock', 'is', 'the', 'best', 'actor', 'in', 'the', 'world'],
 ['New', 'York', 'is', 'a', 'beautiful', 'city']]

#### Al Estilo Scikit

Scikit implementa `bag of words` a través de la clase `CountVectorizer()` la cual contiene muchas opciones para mejorar la tokenización.

In [13]:
bow = CountVectorizer(tokenizer= StemmerTokenizer())
df = bow.fit_transform(docs)

pd.DataFrame(df.toarray(), columns=bow.get_feature_names_out())

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


&  actor  beauti  best  citi  good  like  new  rock  roll  teacher  world  \
0  1      0       0     0     0     1     1    0     2     1        1      0   
1  0      1       0     1     0     0     0    0     1     0        0      1   
2  0      0       1     0     1     0     0    1     0     0        0      0   

   york  
0     0  
1     0  
2     1

Una de las cosas más interesantes que provee son el use de n-gramas, los cuales, en palabras simples, son conjuntos de n-palabras que se concatenan entre si y que se consideran como tokens separados.

Pensemos en `Nueva York`. Cuando se tokeniza Nueva York, se generan dos tokens independientes que a simple vista no tienen relación: `Nueva` `York`.
Al usar n-gramas (en un rango min=1,max=2) , generamos tanto `Nueva` y `York` como también `Nueva York` como un token independiente.

In [14]:
bow = CountVectorizer(tokenizer= StemmerTokenizer(), ngram_range=(1,2))
df = bow.fit_transform(docs)

pd.DataFrame(df.toarray(), columns=bow.get_feature_names_out())

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


&  & roll  actor  actor world  beauti  beauti citi  best  best actor  citi  \
0  1       1      0            0       0            0     0           0     0   
1  0       0      1            1       0            0     1           1     0   
2  0       0      0            0       1            1     0           0     1   

   good  ...  rock  rock &  rock best  rock like  roll  teacher  teacher rock  \
0     1  ...     2       1          0          1     1        1             1   
1     0  ...     1       0          1          0     0        0             0   
2     0  ...     0       0          0          0     0        0             0   

   world  york  york beauti  
0      0     0            0  
1      1     0            0  
2      0     1            1  

[3 rows x 25 columns]

De los resultados, podemos ver que generamos vectores de conteo para cada una de las palabras que conforman el corpus.  Un punto extra que se agrega en esta obtención de frecuencias son los bigramas, que básicamente son el conjunto de palabras de tamaño de aparecen juntas en el texto.

## Codificando los Super{heroes, villanos}  [0.5 Puntos]

<p align="center">
  <img src="https://c.tenor.com/LkQzw7k5DV4AAAAd/anime-hacking.gif" width="300">
</p>

Conociendo ahora que es el proceso de `bag of words`, aplique este modelo de obtención de caracteristicas de la siguiente forma en un pipeline:

- Utilice el tokenizador entregado.
- Obtenga caracteristicas de los unigramas y bigramas del texto (tal como el ejemplo).

```python
bog = CountVectorizer(tokenizer= StemmerTokenizer(),`
                      ngram_range=(1,2) # Este punto es opcional y es para generar bigramas
                      )
```

Finalmente, aplique `MinMaxScaler()` sobre `atributos_de_interes` y concatene el valor obtenido con el matriz de caracteristicas obtenidas con bag of words.

```python
atributos_de_interes = ['intelligence_score', 'strength_score', 'speed_score', 'durability_score', 'power_score', 'combat_score']
```

No es necesario que obtenga un dataframe en concreto con las características solicitadas. Se le recomienda generar un `ColumnTransformer()` para aplicar las transformaciones solicitadas en un pipeline.

**To-Do:**
- [ ] Obtener a traves de Bag of Words (`CountVectorizer`) caracteristicas del resumen de historia de cada personaje.
- [ ] Aplicar `MinMaxScaler` sobre los atributos de interes.

**Respuesta:**

Debido a que en la siguiente parte se pide generar un pipeline, se decide por hacer las transformaciones por separado y de forma simple, con tal de juntarlas en la siguiente sección y poder manejarlas mediante un `Column Transformer`.

In [15]:
# Definir input
docs = df_comics['history_text']

# Generamos stopwords del idioma del corpus
stop_words = stopwords.words('english')

# bag of words (2-gramas)
bag_of_words = CountVectorizer(tokenizer=StemmerTokenizer(), ngram_range=(1,2), stop_words=stop_words) #stop_words='english'

# Transformar y pasar a dataframe
df_bow = bag_of_words.fit_transform(docs)

# Se genera el vocabulario de todo del dataframe
vocab = bag_of_words.get_feature_names_out()

# Se transforma a dataframe para visualizar
df_bow = pd.DataFrame(df_bow.toarray(), columns=vocab)
df_bow

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


!  ! !  ! ''  ! (  ! )  ! ,  ! --  ! .  ! ``  ! alison  ...  �kick� .  \
0     0    0     0    0    0    0     0    0     0         0  ...         0   
1     0    0     0    0    0    0     0    0     0         0  ...         0   
2     0    0     0    0    0    0     0    0     0         0  ...         0   
3     0    0     0    0    0    0     0    0     0         0  ...         0   
4     0    0     0    0    0    0     0    0     0         0  ...         0   
...  ..  ...   ...  ...  ...  ...   ...  ...   ...       ...  ...       ...   
1280  0    0     0    0    0    0     0    0     0         0  ...         0   
1281  1    0     1    0    0    0     0    0     0         0  ...         0   
1282  0    0     0    0    0    0     0    0     0         0  ...         0   
1283  0    0     0    0    0    0     0    0     0         0  ...         0   
1284  0    0     0    0    0    0     0    0     0         0  ...         0   

      �kick� driven  �polic  �polic man�  �white  �white room�  �ǣmortal  \
0                 0       0            0       0             0         0   
1                 0       0            0       0             0         0   
2                 0       0            0       0             0         0   
3                 0       0            0       0             0         0   
4                 0       0            0       0             0         0   
...             ...     ...          ...     ...           ...       ...   
1280              0       0            0       0             0         0   
1281              0       0            0       0             0         0   
1282              0       0            0       0             0         0   
1283              0       0            0       0             0         0   
1284              0       0            0       0             0         0   

      �ǣmortal instruments���  ��wors  ��wors ,  
0                           0       0         0  
1                           0       0         0  
2                           0       0         0  
3                           0       0         0  
4                           0       0         0  
...                       ...     ...       ...  
1280                        0       0         0  
1281                        0       0         0  
1282                        0       0         0  
1283                        0       0         0  
1284                        0       0         0  

[1285 rows x 333382 columns]

In [16]:
# Columnas para aplicar MinMaxScaler
atributos_de_interes = ['intelligence_score', 'strength_score', 'speed_score', 'durability_score', 'power_score', 'combat_score']

# MinMax scaler
preprocessing = ColumnTransformer([
    ('MinMaxScaler', MinMaxScaler(), atributos_de_interes)])

# generar dataframe transformado
df_minmax = pd.DataFrame(
    preprocessing.fit_transform(df_comics[atributos_de_interes]),
    columns=atributos_de_interes)

df_minmax

intelligence_score  strength_score  speed_score  durability_score  \
0                   0.85             0.3         0.60              0.60   
1                   0.80             1.0         0.80              1.00   
2                   0.80             0.5         0.55              0.45   
3                   0.80             0.1         0.25              0.40   
4                   0.90             0.4         0.45              0.55   
...                  ...             ...          ...               ...   
1280                0.90             0.1         0.25              0.30   
1281                0.80             1.0         1.00              1.00   
1282                0.95             0.5         1.00              0.75   
1283                0.75             0.1         1.00              0.30   
1284                0.45             0.8         0.75              0.95   

      power_score  combat_score  
0            0.40          0.70  
1            1.00          0.80  
2            1.00          0.55  
3            0.30          0.50  
4            0.55          0.85  
...           ...           ...  
1280         1.00          0.55  
1281         1.00          0.80  
1282         1.00          0.80  
1283         1.00          0.30  
1284         0.80          0.50  

[1285 rows x 6 columns]

## 1.2 Diseño de Baseline y  Primer Entrenamiento  [1 Puntos]


<p align="center">
  <img src="https://pa1.narvii.com/6374/9eaec1b7bf9157334151452a669516f9a78b954c_hq.gif" width="300">
</p>



Genere un Pipeline con las caracteristicas solicitadas en la sección 1.1, un selector de mejores features `SelectPercentile` con métrica `f_classif` y percentile=90 y un clasificador `MultinomialNB()` por defecto.

Luego, separe el conjunto de datos en un conjunto de entrenamiento y prueba, donde las etiquetas estará dado por el atributo `alignment`.

Entrene el modelo y reporte el desempeño con un `classification_report`. ¿ Nos recomendaría predecir la alineación de BatCow con este clasificador?.

Finalmente, compare el modelo entrenado con un modelo Dummy estratificado y responda: ¿El clasificador entrenado es mejor que el dummy que entrega respuestas al azar?

**To-do:**
- [ ] Realizar un pipeline con las caracteristicas solicitadas en 1.1, ejecutar holdout y aplicar un clasificador `MultinomialNB()`.
- [ ] Entrenar el pipeline, calcular el `classification_report` asociado y comentar los resultados.
- [ ] Entrenar un `DummyClassifier` con estrategia `statified`, calcular el `classification_report` asociado y comentar que implican los scores obtenidos en comparación con los resultados del baseline.

**Respuesta:**

El siguiente código es para obtener el vocabulario de el dataframe en caso de usar el parámetro ngram_range = (1,1), (1,2), (1,3)

In [17]:
# bag of words (1-gramas)
bag_of_words = CountVectorizer(tokenizer=StemmerTokenizer(), ngram_range=(1,1), stop_words=stop_words)
# Transformar y pasar a dataframe
df_bow = bag_of_words.fit_transform(docs)
# Se genera el vocabulario de todo del dataframe
vocab_1_1 = bag_of_words.get_feature_names_out()

# bag of words (2-gramas)
bag_of_words = CountVectorizer(tokenizer=StemmerTokenizer(), ngram_range=(1,2), stop_words=stop_words)
# Transformar y pasar a dataframe
df_bow = bag_of_words.fit_transform(docs)
# Se genera el vocabulario de todo del dataframe
vocab_1_2 = bag_of_words.get_feature_names_out()

# bag of words (3-gramas)
bag_of_words = CountVectorizer(tokenizer=StemmerTokenizer(), ngram_range=(1,3), stop_words=stop_words)
# Transformar y pasar a dataframe
df_bow = bag_of_words.fit_transform(docs)
# Se genera el vocabulario de todo del dataframe
vocab_1_3 = bag_of_words.get_feature_names_out()

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


In [18]:
# Definir input
docs = df_comics['history_text']

# Atributos de interés segun enunciado
atributos_de_interes = ['intelligence_score', 'strength_score', 'speed_score', 'durability_score', 'power_score', 'combat_score']

# Conjuntos train y test
labels = df_comics.loc[:, "alignment"].reset_index(drop=True)

def bow(df, ngram=(1,2)):
  """Realiza bag of words a un documento y concatena las columnas
      atributos_de_interes antes definida.

    Parameters
    ----------
    df : pandas.dataframe
        Base de datos con columna 'history_text' a procesar.

    Returns
    -------
    df_bow:
        pd.dataframe con bow en columna 'history_text' y columnas de interes
        concatenadas.
    """
  # Casos para ver que n-grama se usa y obtener vocabulario
  if ngram==(1,1):
    vocab = vocab_1_1
  if ngram==(1,2):
    vocab = vocab_1_2
  if ngram==(1,3):
    vocab = vocab_1_3
  # documento a procesar mediante bow
  docs = df['history_text']
  # Generamos stopwords del idioma del corpus
  stop_words = stopwords.words('english')
  # bag of words
  bag_of_words = CountVectorizer(tokenizer=StemmerTokenizer(), ngram_range=ngram, stop_words=stop_words, vocabulary=vocab)
  df_bow = bag_of_words.fit_transform(docs)
  # Transformar y pasar a dataframe
  df_bow = pd.DataFrame(df_bow.toarray(), columns=bag_of_words.get_feature_names_out())
  # Concatenar columnas de interes
  df_bow[atributos_de_interes] = df_comics[atributos_de_interes]
  return df_bow

In [19]:
# Definir transformador de columnas (minmax)
column_tranformer = ColumnTransformer(transformers=[('minmax_transform', MinMaxScaler(), atributos_de_interes)], remainder='passthrough')

# Crear pipeline
nb_pipe = Pipeline(
    steps=[
        ('BOW', FunctionTransformer(func=bow)),
        ('Min Max Scaler', column_tranformer),
        ("Selection", SelectPercentile(f_classif, percentile=90)),
        ("NB", MultinomialNB())
    ]
)

In [20]:
# Separar en conjuntos de entrenamiento y prueba
X_train, X_test, y_train, y_test = train_test_split(
    df_comics.drop('alignment', axis=1),
    labels,
    test_size=0.2,
    random_state=4,
    shuffle=True,
    stratify=labels,
)

In [23]:
# Balance de datos en entrenamiento
y_train.value_counts()

Good       595
Bad        343
Neutral     90
Name: alignment, dtype: int64

In [24]:
# Balance de datos en testeo
y_test.value_counts()

Good       148
Bad         86
Neutral     23
Name: alignment, dtype: int64

In [25]:
# Entrenamiento del modelo
X = nb_pipe.fit(X_train, y_train)

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [    22     25     28 ... 333379 333382 333383] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


In [26]:
# Predicciones del modelo
y_pred = nb_pipe.predict(X_test)

# Evaluamos
print(classification_report(y_pred, y_test))

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


              precision    recall  f1-score   support

         Bad       0.19      0.64      0.29        25
        Good       0.96      0.61      0.75       231
     Neutral       0.04      1.00      0.08         1

    accuracy                           0.62       257
   macro avg       0.40      0.75      0.37       257
weighted avg       0.88      0.62      0.70       257



En la celda anterior se puede ver el rendimiento de el clasificador MultinomialNB. Notar que, para la clase "Good" el clasificador tiene un rendimiento decente, sin embargo, esto puede deberse al desbalanceo de datos que posee inicialmente, esto pues esta clase es la que predomina tanto en el entrenamiento como en el conjunto de prueba.
Debido a esto, la clase "Bad" y "Neutral" poseen métricas precarias, indicando que el modelo puede no ser apto para esta tarea o que haga falta una búsqueda de hiperparámetros que mejore su rendimiento.

In [27]:
# Dummy classifier mediante un pipeline
dummy_pipe = Pipeline(
    steps=[
        ('BOW', FunctionTransformer(func=bow)),
        ('Min Max Scaler', column_tranformer),
        ("Dummy", DummyClassifier(strategy="stratified")),
    ]
)

In [28]:
# Entrenamiento del modelo
dummy_pipe.fit(X_train, y_train)

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


Pipeline(steps=[('BOW',
                 FunctionTransformer(func=<function bow at 0x7f63cbf36b90>)),
                ('Min Max Scaler',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('minmax_transform',
                                                  MinMaxScaler(),
                                                  ['intelligence_score',
                                                   'strength_score',
                                                   'speed_score',
                                                   'durability_score',
                                                   'power_score',
                                                   'combat_score'])])),
                ('Dummy', DummyClassifier(strategy='stratified'))])

In [29]:
# Predicciones del modelo dummy
y_pred = dummy_pipe.predict(X_test)

# Evaluamos
print(classification_report(y_pred, y_test))

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


              precision    recall  f1-score   support

         Bad       0.35      0.28      0.31       106
        Good       0.49      0.55      0.52       132
     Neutral       0.04      0.05      0.05        19

    accuracy                           0.40       257
   macro avg       0.30      0.30      0.29       257
weighted avg       0.40      0.40      0.40       257



Como era esperable, la clase "Neutral" tiene un rendimiento nulo, ya que la cantidad de personajes que poseen esta clase es muy baja tanto en el conjunto de entrenamiento como el de prueba.
Por otro lado, en comparación al modelo anterior, se puede apreciar que el modelo MultinomimalNB es ligeramente mejor que un clasificador al azar, sin embargo, no son métricas con las cuales se puede confiar la tarea final de asignarle una clase a batcow.

## 1.3 Busqueda del Mejor Modelo con Grid Search [4 Puntos]

<p align="center">
  <img src="https://media1.tenor.com/images/70fdfeea52a8e2e4505498c230a0d2f9/tenor.gif?itemid=5134219" width="250">
</p>

No conformes con el rendimiento obtenido en la sección 1.2, el cuerpo docente les pide que realicen un **`HalvingGridSearchCV`** con diferentes parámetros para mejorar el rendimiento de la clasificación. Para esto, se le solicita que defina:

- Tres clasificadores distintos en donde varie sus parámetros. Considere usar modelos clásicos como también los basados en ensamblaje.
- Modificar `n-gram` range del `CountVectorizer` probando `(1,1), (1,2) y (1,3)`. Examinar también los otros parámetros de CountVectorizer como por ejemplo `max_df`, `min_df`, etc... ([Documentación aquí](https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.CountVectorizer.html))
- Seleccionar las columnas que contribuyen con la mayor información para la clasificación con `SelectPercentile` en los percentiles `[20, 40, 60, 80]` (puede usar la métrica que usted quiera).
- Reporte la mejor combinación encontrada y justifique por qué cree que es la mejor según el clasificador usado, la cantidad de columnas seleccionadas y los parámetros de CountVectorizer seleccionados por GridSearch.

A continuación, un ejemplo de parametros para GridSearch para una búsqueda de 3 clasificadores distintos:

```python
params = [
       # clasificador 1 + hiperparámetros
       {'clf': classificator1(),
        'clf__penalty': ['ovr'],
       # clasificador 1 + hiperparámetros
       {'clf': classificator2(),
        'clf__n_estimators': [200]},
       # clasificador 1 + hiperparámetros
       {'clf': classificator3(),
        ...
       }
       ]
```

**Nota 1**: Puede ver los parámetros modificables aplicando el método get_params() sobre su pipeline. Ver la clase de GridSearch para mayor información sobre la sintáxis de las grillas.

**Nota 2**: Recuerde inicializar los clasificadores con un random state definido.

**Nota 3**: Puede usar en `HalvingGridSearchCV` el parámetro `verbose=10` para ver que GridSearch le indique el estado de su ejecución.

**Nota 3:** El GridSearch puede tomar tiempos de búsqueda exorbitantes, por lo que se le recomienda no agrandar mucho el espacio de búsqueda, dejar corriendo el código y tomarse un tecito.

**Respuesta:**

A continuación se genera a grilla de parámetros que se probarán en los clasificadores para medir sus resultados finales.
Se prueban distintos clasificadores, con algunos hiperparámetros diferentes. Se prueban otros porcentajes de percentiles mediante la métrica f_classif, y por último, se prueba con otros número de n-gramas en las palabras del corpus.

In [30]:
# Función para entrenar y evaluar un clasificador (Github clases)

def train_and_evaluate(
    pipe, print_=True, X_train=X_train, y_train=y_train, X_test=X_test, y_test=y_test
):

    # notar que los datasets son parámetros por defecto.

    pipe.fit(X_train, y_train)
    y_pred = pipe.predict(X_test)

    if print_:
        print("Matriz de confusión: \n")
        print(confusion_matrix(y_test, y_pred, labels=pipe.classes_))
        print("\nReporte de Clasificación: \n")
        print(
            classification_report(y_test, y_pred, target_names=pipe.classes_),
        )

    return f1_score(y_test, y_pred, average="macro")

In [63]:
# Modelos a probar

params_model = [
              {'RF': RandomForestClassifier(random_state=1),
                'Model__n_estimators': [10, 100]},
              {'SVM': SVC(random_state=1),
                'Model__kernel': ['linear', 'poly']},
              {'Tree': DecisionTreeClassifier(random_state=1),
                'Model__max_depth': [10, 50]}
              ]

lista_modelos = ['RF', 'SVM', 'Tree']

print(params_model)

{'BOW__kw_args': [{'ngram': (1, 1)}, {'ngram': (1, 2)}, {'ngram': (1, 3)}], 'Selection__percentile': [20, 40, 60, 80]}
[{'RF': RandomForestClassifier(random_state=1), 'Model__n_estimators': [10, 100]}, {'SVM': SVC(random_state=1), 'Model__kernel': ['linear', 'poly']}, {'Tree': DecisionTreeClassifier(random_state=1), 'Model__max_depth': [10, 50]}]


In [ ]:
# Esta celda de código demora en ejecutarse y usa bastante memoria RAM !!

# Lista para guardar los modelos
HGS = []

# Recorrer modelos y parámetros
for i in range(len(lista_modelos)):
  model = params_model[i][lista_modelos[i]]
  pipe = Pipeline(
    steps=[
        ('BOW', FunctionTransformer(func=bow)),
        ('Min Max Scaler', column_tranformer),
        ("Selection", SelectPercentile(f_classif)),
        ("Model", model)
    ]
  )

  # Definir grilla manualmente
  param_model = {}
  for clave, valor in params_model[i].items():
      if isinstance(valor, list) and len(valor) > 1:
        param_model[clave] = valor

  grilla = {**param_model,
    **{'BOW__kw_args': [{'ngram': value} for value in [(1,1), (1,2), (1,3)]],
    'Selection__percentile': [20, 40, 60, 80]}
  }
  print('Grilla:', grilla)
  # Búsqueda de hiperparámetros
  hgs = HalvingGridSearchCV(pipe, grilla, scoring='f1_macro', verbose=10, cv=3, factor=8)
  # Entrenar
  train_and_evaluate(hgs)
  # Guardar modelo
  HGS.append(hgs)

Grilla: {'Model__n_estimators': [10, 100], 'BOW__kw_args': [{'ngram': (1, 1)}, {'ngram': (1, 2)}, {'ngram': (1, 3)}], 'Selection__percentile': [20, 40, 60, 80]}
n_iterations: 2
n_required_iterations: 2
n_possible_iterations: 2
min_resources_: 128
max_resources_: 1028
aggressive_elimination: False
factor: 8
----------
iter: 0
n_candidates: 24
n_resources: 128
Fitting 3 folds for each of 24 candidates, totalling 72 fits
[CV 1/3; 1/24] START BOW__kw_args={'ngram': (1, 1)}, Model__n_estimators=10, Selection__percentile=20


/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [    7    10    13 ... 22762 22763 22764] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw
/usr/local/lib/python3.10/dist-packages/sklearn/feature_e

[CV 1/3; 1/24] END BOW__kw_args={'ngram': (1, 1)}, Model__n_estimators=10, Selection__percentile=20;, score=(train=1.000, test=0.242) total time=   2.9s
[CV 2/3; 1/24] START BOW__kw_args={'ngram': (1, 1)}, Model__n_estimators=10, Selection__percentile=20


/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [   13    14    15 ... 22761 22762 22763] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw
/usr/local/lib/python3.10/dist-packages/sklearn/feature_e

[CV 2/3; 1/24] END BOW__kw_args={'ngram': (1, 1)}, Model__n_estimators=10, Selection__percentile=20;, score=(train=0.991, test=0.231) total time=   2.3s
[CV 3/3; 1/24] START BOW__kw_args={'ngram': (1, 1)}, Model__n_estimators=10, Selection__percentile=20


...

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [    11     13     17 ... 865574 865575 865576] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw
/usr/local/lib/python3.10/dist-packages/sklearn/fea

[CV 2/3; 3/3] END BOW__kw_args={'ngram': (1, 3)}, Model__max_depth=50, Selection__percentile=20;, score=(train=1.000, test=0.396) total time= 1.1min
[CV 3/3; 3/3] START BOW__kw_args={'ngram': (1, 3)}, Model__max_depth=50, Selection__percentile=20


/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [     7      8      9 ... 865580 865581 865582] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw
/usr/local/lib/python3.10/dist-packages/sklearn/fea

[CV 3/3; 3/3] END BOW__kw_args={'ngram': (1, 3)}, Model__max_depth=50, Selection__percentile=20;, score=(train=1.000, test=0.365) total time= 1.1min


/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


In [ ]:
# Código para ver los mejores scores y parámetros usados para cada modelo definido arriba
for model in HGS:
  print('best score:', model.best_score_)
  print('best params', model.best_params_)

Como se puede ver en la ejecución de HalvingGridSearchCV, se probaron los modelos de Random Forest, Support Vector Machine y Decision Tree. Por otro lado, se revisó un hiperparámetro para cada uno de los modelos entre un rango de 2 o 3 diferentes.
Así mismo, se probaron (para cada modelo) distintos rangos de percentiles y con una diferente confuguración de n-gramas.

Así, se puede ver que los resultados mejoraron con respecto al clasificador inicial que se tenía en la sección anterior. Con esto, se puede concluir que el mejor clasificador para esta tarea viene siendo SVM con hiperparámetros kernel='linear', usando percentil=60 (esto no afectaba deemasiado el resultado) junto con un ngram=(1,1).

## 1.4 Predicción del datos sin etiquetado  [0.5 puntos]

<p align="center">
  <img src="https://pbs.twimg.com/media/DolotxUUYAAbg7f.jpg" width="350">
</p>


LLego el momento de predecir
`Vergil`, `Gorilla Girl` y `Batcow`


**Nota:** Recuerde que pueden existir campos vacios en `history_text`, por lo que se les recomienda borrar los nan.

**Respuesta:**

In [21]:
# Borrar filas con valores nan en columna 'history_text'
df_comics_no_label = df_comics_no_label.dropna(subset=['history_text']).reset_index(drop=True) # eliminar ejemplos sin historia
df_comics_no_label.head()

Unnamed: 0              name    real_name        full_name overall_score  \
0           1     514A (Gotham)  Bruce Wayne              NaN            10   
1          17             A'dal          NaN              NaN             7   
2          27  Agent Zero (FOX)  David North              NaN             6   
3          31        Ajax (FOX)      Francis  Francis Freeman             7   
4          46   A.M.A.Z.O. (CW)          NaN              NaN            22   

                                        history_text  \
0  He was one of the many prisoners of Indian Hil...   
1  As with most of the naaru, little is known of ...   
2  During mid-late 1973, Zero was a member of Tea...   
3  Ajax (born Francis Freeman) was a human who ga...   
4  The Anti Meta-human Adaptive Zootomic Organism...   

                                         powers_text  intelligence_score  \
0                                                NaN                 100   
1                                                NaN                  85   
2  Zero can absorb kinetic energy to further incr...                  90   
3  Ajax has claimed that the procedure to obtain ...                  85   
4  With its metallic body, it easily overpowered ...                  90   

   strength_score  speed_score  ...  has_flight  has_accelerated_healing  \
0              20           30  ...         0.0                      0.0   
1              30           70  ...         0.0                      0.0   
2              10           25  ...         0.0                      0.0   
3              25           45  ...         0.0                      0.0   
4             100          100  ...         1.0                      0.0   

   has_weapons_master has_intelligence has_reflexes has_super_speed  \
0                 0.0              0.0          1.0             0.0   
1                 0.0              0.0          0.0             0.0   
2                 0.0              0.0          1.0             0.0   
3                 1.0              1.0          1.0             0.0   
4                 1.0              0.0          0.0             0.0   

  has_durability has_stamina has_agility  has_super_strength  
0            1.0         0.0         0.0                 1.0  
1            0.0         0.0         0.0                 0.0  
2            0.0         0.0         1.0                 0.0  
3            1.0         0.0         0.0                 1.0  
4            0.0         0.0         0.0                 0.0  

[5 rows x 82 columns]

In [22]:
# Definir inputs a predecir

batcow = df_comics_no_label[df_comics_no_label['name'] == 'Batcow']
batcow = batcow[['history_text'] + atributos_de_interes].drop_duplicates()

Vergil = df_comics_no_label[df_comics_no_label['name'] == 'Vergil']
Vergil = Vergil[['history_text'] + atributos_de_interes]

Gorilla_Girl = df_comics_no_label[df_comics_no_label['name'] == 'Gorilla Girl']
Gorilla_Girl = Gorilla_Girl[['history_text'] + atributos_de_interes]

batcow

history_text  intelligence_score  \
14  Bat-Cow was originally a cow that was found by...                  70   

    strength_score  speed_score  durability_score  power_score  combat_score  
14              10           25                20           10            20

In [23]:
Vergil

history_text  intelligence_score  \
71  Vergil, later also known as Nelo Angelo, is on...                  90   

    strength_score  speed_score  durability_score  power_score  combat_score  
71              75           95                90          100           100

In [24]:
Gorilla_Girl

history_text  intelligence_score  \
37  A carnival performer with the ability to turn ...                  90   

    strength_score  speed_score  durability_score  power_score  combat_score  
37              35           60                60           45           100

In [25]:
# Definir conjunto a predecir "alignment"
X_no_label = pd.concat([batcow, Gorilla_Girl, Vergil], axis=0)
X_no_label

history_text  intelligence_score  \
14  Bat-Cow was originally a cow that was found by...                  70   
37  A carnival performer with the ability to turn ...                  90   
71  Vergil, later also known as Nelo Angelo, is on...                  90   

    strength_score  speed_score  durability_score  power_score  combat_score  
14              10           25                20           10            20  
37              35           60                60           45           100  
71              75           95                90          100           100

In [28]:
# Clasificador con mejores métricas según HalvingGridSearchCV

# Crear pipeline
pipe = Pipeline(
    steps=[
        ('BOW', FunctionTransformer(func=bow, kw_args={'ngram': (1,1)})),
        ('Min Max Scaler', column_tranformer),
        ("Selection", SelectPercentile(f_classif, percentile=60)),
        ("NB", SVC(kernel='linear'))
    ]
)


In [29]:
# Entrenamiento del modelo
pipe.fit(X_train, y_train)

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:112: UserWarning: Features [   27    30    33 ... 22742 22760 22762] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx, UserWarning)
/usr/local/lib/python3.10/dist-packages/sklearn/feature_selection/_univariate_selection.py:113: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


Pipeline(steps=[('BOW',
                 FunctionTransformer(func=<function bow at 0x7fb297927b50>,
                                     kw_args={'ngram': (1, 1)})),
                ('Min Max Scaler',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('minmax_transform',
                                                  MinMaxScaler(),
                                                  ['intelligence_score',
                                                   'strength_score',
                                                   'speed_score',
                                                   'durability_score',
                                                   'power_score',
                                                   'combat_score'])])),
                ('Selection', SelectPercentile(percentile=60)),
                ('NB', SVC(kernel='linear'))])

In [32]:
# Predicciones del modelo en conjunto con labels ya asignado
y_pred = pipe.predict(X_test)

# Evaluamos
print(classification_report(y_pred, y_test))

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(


              precision    recall  f1-score   support

         Bad       0.51      0.58      0.54        76
        Good       0.79      0.75      0.77       157
     Neutral       0.26      0.25      0.26        24

    accuracy                           0.65       257
   macro avg       0.52      0.52      0.52       257
weighted avg       0.66      0.65      0.65       257



In [31]:
# Predicciones del modelo al nuevo conjunto
y_pred = pipe.predict(X_no_label)
print('\n Las predicciones de batcow, vergil y gorilla girl son', y_pred, 'respectivamente \n')

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:409: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ["'d", "'ll", "'re", "'s", "'ve", 'could', 'might', 'must', "n't", 'need', 'sha', 'wo', 'would'] not in stop_words.
  warnings.warn(



 Las predicciones de batcow, vergil y gorilla girl son ['Good' 'Bad' 'Neutral'] respectivamente 



Así, se puede concluir que gracias a `HalvingGridSearchCV`, el modelo ha mejorado sus métricas en general, sin embargo, esto viene con una gran cantidad de tiempo consumida por este algoritmo.

Por otro lado, se espera que usando grillas de hiperparámetros más grandes y eligiendo modelos que mejor se adapten a este problema, junto con otros hiperparámetros en la función de búsqueda mejoren el rendimiento general de este problema.

A futuro se pueden implementar otras técnicas del área de NLP junto con modelos más robustos como pueden ser redes neuronales (CNN, RNN) o incluso transformers, donde se aprecia en la práctica que son buenos modelos para este tipo de problemas.

<p align="center">
  <img src="https://media1.tenor.com/images/fb5bf7cc5a4acb91b4177672886a88ba/tenor.gif?itemid=5591338">
</p>

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=87110296-876e-426f-b91d-aaf681223468' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>